In [1]:
#import wradlib as wrl
import os
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as pl
import warnings
warnings.filterwarnings('ignore')
try:
    get_ipython().magic("matplotlib inline")
except:
    pl.ion()
from scipy import interpolate
import datetime as dt
import glob
import json
from datetime import datetime
from datetime import timedelta

import pandas as pd

import metpy.calc as mpcalc
from metpy.cbook import get_test_data
from metpy.plots import add_metpy_logo, Hodograph, SkewT
from metpy.units import units

import numpy as np
import xarray as xr

from rpy2.robjects.packages import importr
from rpy2.robjects import r,pandas2ri
import rpy2.robjects as robjects
import rpy2.robjects.numpy2ri
rpy2.robjects.numpy2ri.activate()
pandas2ri.activate()
#importr('thunder', lib_loc="/home/lms/R/x86_64-pc-linux-gnu-library/4.0/")
base = importr('base')
print(base._libPaths())
importr('thunder')

[1] "/home/lmathias/anaconda3/envs/metpy/lib/R/library"



rpy2.robjects.packages.Package as a <module 'thunder'>

In [2]:
file_dir = '/data/iconeu/soundings/'

# Changing the directory
os.chdir(file_dir)

data = xr.open_dataset('icon_pl.nc')

data_sfc = xr.open_dataset('icon_sfc.nc')

data_sfc2 = xr.open_dataset('icon_hsurf.nc')

# View a summary of the Dataset
#print(data.time.values[0])
print(data)
print(data_sfc2)


<xarray.Dataset>
Dimensions:    (longitude: 1097, latitude: 657, level: 18, time: 50)
Coordinates:
  * longitude  (longitude) float32 -23.5 -23.44 -23.38 ... 44.88 44.94 45.0
  * latitude   (latitude) float32 29.5 29.56 29.62 29.69 ... 70.38 70.44 70.5
  * level      (level) int32 100 150 200 250 300 400 ... 875 900 925 950 1000
  * time       (time) datetime64[ns] 2022-06-09T12:00:00 ... 2022-06-11T13:00:00
Data variables:
    v          (time, level, latitude, longitude) float32 ...
    u          (time, level, latitude, longitude) float32 ...
    t          (time, level, latitude, longitude) float32 ...
    r          (time, level, latitude, longitude) float32 ...
    z          (time, level, latitude, longitude) float32 ...
Attributes:
    Conventions:  CF-1.6
    history:      2022-06-09 15:52:38 GMT by grib_to_netcdf-2.6.0: grib_to_ne...
<xarray.Dataset>
Dimensions:    (longitude: 1097, latitude: 657, time: 1)
Coordinates:
  * longitude  (longitude) float32 -23.5 -23.44 -23.38 ..

In [3]:
for i in range(49):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data_sfc['t2m'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=0)
    print(timeinit)

    temp = data['t']
    rhum = data['r']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']
    #press = np.sort(press)

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    #pwat = data_sfc['tcwv']
    #deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcheight = data_sfc2['h']
    #msl =  data_sfc5['msl']

    ##############################################################

    lat = 49.625
    lon = 6.125

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #msl = msl.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    rhum = rhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcheight = sfcheight.metpy.loc[{ 'latitude': lat, 'longitude': lon}]
    #pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[17] = sfctemp
    uwind[17] = sfcuwind
    vwind[17] = sfcvwind
    #geopot[17] = sfcgeopot
    press = np.where(press == 1000 , np.round(sfcpress/100) ,press)
    #press = press*units.hPa
    #msl = (msl.data)/100*units.hPa

    #sfcpress.data=92400
    
    if sfcpress.item(0) <= 95100:
                temp = np.delete(temp,16)
                rhum = np.delete(rhum,16)
                geopot = np.delete(geopot,16)
                uwind = np.delete(uwind,16)
                vwind = np.delete(vwind,16)
                press = np.delete(press,16)
                
    if sfcpress.item(0) <= 92600:
                temp = np.delete(temp,15)
                rhum = np.delete(rhum,15)
                geopot = np.delete(geopot,15)
                uwind = np.delete(uwind,15)
                vwind = np.delete(vwind,15)
                press = np.delete(press,15)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    rhum = rhum.data[::-1]*units('percent')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    tempc = temp-273.15
    tempc = tempc.data[::-1]*units.degC
    sfcheight=sfcheight.data[::]*units.meter

    dew = mpcalc.dewpoint_from_relative_humidity(tempc, rhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    #dew[0] = sfcdew*units.degC
    #pwat = pwat.data.item()
    #pwat = pwat*units.mm
    #deg0l = deg0l.data.item()
    #deg0l = deg0l*units.meters

    #pressdiff = msl-press[0]
    #sfcheight = (np.log(msl/press[0])*8000)*units.meter

#    print(sfcheight)
#     print(press)
#     print(tempc)
#     print(geopot)
#     print(dew)

    height = mpcalc.geopotential_to_height(geopot)
    height2 = height.to('feet')
    height[0]=sfcheight
    
    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(tempc.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i*1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='icon_sounding_luxcity_%s.png' %time2,title='ICON-EU | Luxembourg | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   307   521   746   976  1210  1449  1694  1945  2201  3017  4242  5646
[13]  7295  9304 10505 11929 13799 16449



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   307   519   743   973  1208  1447  1692  1943  2199  3016  4240  5643
[13]  7294  9302 10502 11929 13799 16448



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2022-06-08 06:00:00
 [1]   307   615   838  1065  1298  1536  1781  2033  2291  3113  4331  5756
[13]  7444  9497 10731 12187 14000 16558



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   307   619   841  1069  1301  1540  1785  2037  2296  3117  4338  5764
[13]  7451  9501 10736 12192 14000 16558



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   307   622   845  1073  1306  1545  1791  2043  2302  3123  4346  5772
[13]  7456  9505 10741 12196 14003 16561



In [4]:
for i in range(49):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=0)
    print(timeinit)

    temp = data['t']
    rhum = data['r']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']
    #press = np.sort(press)

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    #pwat = data_sfc['tcwv']
    #deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcheight = data_sfc2['h']
    #msl =  data_sfc5['msl']

    ##############################################################

    lat = 50.125
    lon = 6.0

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #msl = msl.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    rhum = rhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcheight = sfcheight.metpy.loc[{ 'latitude': lat, 'longitude': lon}]
    #pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[17] = sfctemp
    uwind[17] = sfcuwind
    vwind[17] = sfcvwind
    #geopot[17] = sfcgeopot
    press = np.where(press == 1000 , np.round(sfcpress/100) ,press)
    #press = press*units.hPa
    #msl = (msl.data)/100*units.hPa

    #sfcpress.data=92400
    
    if sfcpress.item(0) <= 95100:
                temp = np.delete(temp,16)
                rhum = np.delete(rhum,16)
                geopot = np.delete(geopot,16)
                uwind = np.delete(uwind,16)
                vwind = np.delete(vwind,16)
                press = np.delete(press,16)
                
    if sfcpress.item(0) <= 92600:
                temp = np.delete(temp,15)
                rhum = np.delete(rhum,15)
                geopot = np.delete(geopot,15)
                uwind = np.delete(uwind,15)
                vwind = np.delete(vwind,15)
                press = np.delete(press,15)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    rhum = rhum.data[::-1]*units('percent')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    tempc = temp-273.15
    tempc = tempc.data[::-1]*units.degC
    sfcheight=sfcheight.data[::]*units.meter

    dew = mpcalc.dewpoint_from_relative_humidity(tempc, rhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    #dew[0] = sfcdew*units.degC
    #pwat = pwat.data.item()
    #pwat = pwat*units.mm
    #deg0l = deg0l.data.item()
    #deg0l = deg0l*units.meters

    #pressdiff = msl-press[0]
    #sfcheight = (np.log(msl/press[0])*8000)*units.meter

#    print(sfcheight)
#     print(press)
#     print(tempc)
#     print(geopot)
#     print(dew)

    height = mpcalc.geopotential_to_height(geopot)
    height2 = height.to('feet')
    height[0]=sfcheight

    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(tempc.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i*1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='icon_sounding_tvierges_%s.png' %time2,title='ICON-EU | Troisvierges | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   489   517   740   969  1204  1443  1688  1939  2196  3011  4235  5637
[13]  7284  9288 10487 11917 13792 16445



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   489   515   739   968  1202  1441  1686  1937  2193  3009  4232  5634
[13]  7282  9286 10484 11917 13792 16445



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2022-06-08 06:00:00
 [1]   489   611   833  1060  1293  1531  1776  2028  2287  3109  4328  5753
[13]  7439  9491 10724 12180 13995 16555



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   489   612   834  1062  1295  1534  1780  2033  2292  3112  4335  5761
[13]  7446  9494 10728 12183 13996 16557



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   489   617   839  1067  1300  1540  1786  2038  2298  3118  4343  5768
[13]  7452  9499 10733 12187 13998 16560



In [5]:
for i in range(49):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=0)
    print(timeinit)

    temp = data['t']
    rhum = data['r']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']
    #press = np.sort(press)

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    #pwat = data_sfc['tcwv']
    #deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcheight = data_sfc2['h']
    #msl =  data_sfc5['msl']

    ##############################################################

    lat = 49.375
    lon = 6.1875

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #msl = msl.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    rhum = rhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcheight = sfcheight.metpy.loc[{ 'latitude': lat, 'longitude': lon}]
    #pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[17] = sfctemp
    uwind[17] = sfcuwind
    vwind[17] = sfcvwind
    #geopot[17] = sfcgeopot
    press = np.where(press == 1000 , np.round(sfcpress/100) ,press)
    #press = press*units.hPa
    #msl = (msl.data)/100*units.hPa

    #sfcpress.data=92400
    
    if sfcpress.item(0) <= 95100:
                temp = np.delete(temp,16)
                rhum = np.delete(rhum,16)
                geopot = np.delete(geopot,16)
                uwind = np.delete(uwind,16)
                vwind = np.delete(vwind,16)
                press = np.delete(press,16)
                
    if sfcpress.item(0) <= 92600:
                temp = np.delete(temp,15)
                rhum = np.delete(rhum,15)
                geopot = np.delete(geopot,15)
                uwind = np.delete(uwind,15)
                vwind = np.delete(vwind,15)
                press = np.delete(press,15)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    rhum = rhum.data[::-1]*units('percent')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    tempc = temp-273.15
    tempc = tempc.data[::-1]*units.degC
    sfcheight=sfcheight.data[::]*units.meter

    dew = mpcalc.dewpoint_from_relative_humidity(tempc, rhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    #dew[0] = sfcdew*units.degC
    #pwat = pwat.data.item()
    #pwat = pwat*units.mm
    #deg0l = deg0l.data.item()
    #deg0l = deg0l*units.meters

    #pressdiff = msl-press[0]
    #sfcheight = (np.log(msl/press[0])*8000)*units.meter

#    print(sfcheight)
#     print(press)
#     print(tempc)
#     print(geopot)
#     print(dew)

    height = mpcalc.geopotential_to_height(geopot)
    height2 = height.to('feet')
    height[0]=sfcheight

    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(tempc.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i*1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='icon_sounding_tville_%s.png' %time2,title='ICON-EU | Thionville | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   171   524   748   978  1212  1452  1696  1947  2204  3019  4246  5650
[13]  7301  9311 10513 11935 13803 16450



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   171   521   746   976  1210  1450  1695  1945  2202  3019  4244  5647
[13]  7298  9309 10509 11935 13803 16450



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2022-06-08 06:00:00
 [1]   171   618   841  1068  1301  1539  1784  2035  2294  3115  4332  5759
[13]  7446  9499 10734 12191 14003 16558



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   171   621   844  1071  1304  1543  1788  2040  2299  3119  4339  5766
[13]  7453  9504 10739 12195 14004 16559



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   171   624   847  1075  1308  1548  1793  2045  2304  3125  4347  5774
[13]  7459  9509 10745 12199 14006 16563



In [6]:
for i in range(49):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=0)
    print(timeinit)

    temp = data['t']
    rhum = data['r']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']
    #press = np.sort(press)

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    #pwat = data_sfc['tcwv']
    #deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcheight = data_sfc2['h']
    #msl =  data_sfc5['msl']

    ##############################################################

    lat = 49.75
    lon = 6.625

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #msl = msl.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    rhum = rhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcheight = sfcheight.metpy.loc[{ 'latitude': lat, 'longitude': lon}]
    #pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[17] = sfctemp
    uwind[17] = sfcuwind
    vwind[17] = sfcvwind
    #geopot[17] = sfcgeopot
    press = np.where(press == 1000 , np.round(sfcpress/100) ,press)
    #press = press*units.hPa
    #msl = (msl.data)/100*units.hPa

    #sfcpress.data=92400
    
    if sfcpress.item(0) <= 95100:
                temp = np.delete(temp,16)
                rhum = np.delete(rhum,16)
                geopot = np.delete(geopot,16)
                uwind = np.delete(uwind,16)
                vwind = np.delete(vwind,16)
                press = np.delete(press,16)
                
    if sfcpress.item(0) <= 92600:
                temp = np.delete(temp,15)
                rhum = np.delete(rhum,15)
                geopot = np.delete(geopot,15)
                uwind = np.delete(uwind,15)
                vwind = np.delete(vwind,15)
                press = np.delete(press,15)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    rhum = rhum.data[::-1]*units('percent')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    tempc = temp-273.15
    tempc = tempc.data[::-1]*units.degC
    sfcheight=sfcheight.data[::]*units.meter

    dew = mpcalc.dewpoint_from_relative_humidity(tempc, rhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    #dew[0] = sfcdew*units.degC
    #pwat = pwat.data.item()
    #pwat = pwat*units.mm
    #deg0l = deg0l.data.item()
    #deg0l = deg0l*units.meters

    #pressdiff = msl-press[0]
    #sfcheight = (np.log(msl/press[0])*8000)*units.meter

#    print(sfcheight)
#     print(press)
#     print(tempc)
#     print(geopot)
#     print(dew)

    height = mpcalc.geopotential_to_height(geopot)
    height2 = height.to('feet')
    height[0]=sfcheight
    
    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(tempc.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i*1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='icon_sounding_trier_%s.png' %time2,title='ICON-EU | Trier | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   230   523   747   976  1210  1450  1695  1946  2202  3016  4242  5646
[13]  7296  9306 10507 11928 13799 16448



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   230   521   745   975  1209  1448  1693  1944  2200  3015  4240  5644
[13]  7294  9303 10503 11928 13800 16448



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2022-06-08 06:00:00
 [1]   230   616   838  1066  1298  1536  1780  2031  2289  3110  4327  5749
[13]  7434  9486 10721 12178 13996 16555



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   230   619   841  1069  1301  1539  1784  2036  2294  3115  4332  5757
[13]  7443  9493 10727 12182 13998 16557



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   230   622   845  1072  1305  1544  1789  2041  2300  3121  4340  5765
[13]  7450  9498 10732 12187 13999 16561



In [7]:
for i in range(49):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=0)
    print(timeinit)

    temp = data['t']
    rhum = data['r']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']
    #press = np.sort(press)

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    #pwat = data_sfc['tcwv']
    #deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcheight = data_sfc2['h']
    #msl =  data_sfc5['msl']

    ##############################################################

    lat = 49.75
    lon = 6.125

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #msl = msl.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    rhum = rhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcheight = sfcheight.metpy.loc[{ 'latitude': lat, 'longitude': lon}]
    #pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[17] = sfctemp
    uwind[17] = sfcuwind
    vwind[17] = sfcvwind
    #geopot[17] = sfcgeopot
    press = np.where(press == 1000 , np.round(sfcpress/100) ,press)
    #press = press*units.hPa
    #msl = (msl.data)/100*units.hPa

    #sfcpress.data=92400
    
    if sfcpress.item(0) <= 95100:
                temp = np.delete(temp,16)
                rhum = np.delete(rhum,16)
                geopot = np.delete(geopot,16)
                uwind = np.delete(uwind,16)
                vwind = np.delete(vwind,16)
                press = np.delete(press,16)
                
    if sfcpress.item(0) <= 92600:
                temp = np.delete(temp,15)
                rhum = np.delete(rhum,15)
                geopot = np.delete(geopot,15)
                uwind = np.delete(uwind,15)
                vwind = np.delete(vwind,15)
                press = np.delete(press,15)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    rhum = rhum.data[::-1]*units('percent')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    tempc = temp-273.15
    tempc = tempc.data[::-1]*units.degC
    sfcheight=sfcheight.data[::]*units.meter

    dew = mpcalc.dewpoint_from_relative_humidity(tempc, rhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    #dew[0] = sfcdew*units.degC
    #pwat = pwat.data.item()
    #pwat = pwat*units.mm
    #deg0l = deg0l.data.item()
    #deg0l = deg0l*units.meters

    #pressdiff = msl-press[0]
    #sfcheight = (np.log(msl/press[0])*8000)*units.meter

#    print(sfcheight)
#     print(press)
#     print(tempc)
#     print(geopot)
#     print(dew)

    height = mpcalc.geopotential_to_height(geopot)
    height2 = height.to('feet')
    height[0]=sfcheight

    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(tempc.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i*1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='icon_sounding_mersch_%s.png' %time2,title='ICON-EU | Mersch | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   290   520   744   974  1208  1447  1692  1943  2200  3015  4240  5643
[13]  7293  9301 10501 11926 13797 16448



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   290   518   742   972  1206  1446  1690  1941  2198  3014  4238  5641
[13]  7291  9299 10498 11926 13797 16448



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2022-06-08 06:00:00
 [1]   290   614   837  1064  1297  1535  1780  2032  2290  3112  4330  5755
[13]  7443  9495 10729 12185 13999 16557



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   290   617   840  1067  1300  1539  1784  2036  2295  3116  4337  5763
[13]  7449  9499 10734 12190 13999 16558



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   290   620   843  1071  1304  1544  1789  2041  2301  3122  4345  5771
[13]  7455  9503 10739 12194 14001 16561



In [8]:
for i in range(49):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=0)
    print(timeinit)

    temp = data['t']
    rhum = data['r']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']
    #press = np.sort(press)

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    #pwat = data_sfc['tcwv']
    #deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcheight = data_sfc2['h']
    #msl =  data_sfc5['msl']

    ##############################################################

    lat = 49.75
    lon = 5.625

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #msl = msl.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    rhum = rhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcheight = sfcheight.metpy.loc[{ 'latitude': lat, 'longitude': lon}]
    #pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[17] = sfctemp
    uwind[17] = sfcuwind
    vwind[17] = sfcvwind
    #geopot[17] = sfcgeopot
    press = np.where(press == 1000 , np.round(sfcpress/100) ,press)
    #press = press*units.hPa
    #msl = (msl.data)/100*units.hPa

    #sfcpress.data=92400
    
    if sfcpress.item(0) <= 95100:
                temp = np.delete(temp,16)
                rhum = np.delete(rhum,16)
                geopot = np.delete(geopot,16)
                uwind = np.delete(uwind,16)
                vwind = np.delete(vwind,16)
                press = np.delete(press,16)
                
    if sfcpress.item(0) <= 92600:
                temp = np.delete(temp,15)
                rhum = np.delete(rhum,15)
                geopot = np.delete(geopot,15)
                uwind = np.delete(uwind,15)
                vwind = np.delete(vwind,15)
                press = np.delete(press,15)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    rhum = rhum.data[::-1]*units('percent')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    tempc = temp-273.15
    tempc = tempc.data[::-1]*units.degC
    sfcheight=sfcheight.data[::]*units.meter

    dew = mpcalc.dewpoint_from_relative_humidity(tempc, rhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    #dew[0] = sfcdew*units.degC
    #pwat = pwat.data.item()
    #pwat = pwat*units.mm
    #deg0l = deg0l.data.item()
    #deg0l = deg0l*units.meters

    #pressdiff = msl-press[0]
    #sfcheight = (np.log(msl/press[0])*8000)*units.meter

#    print(sfcheight)
#     print(press)
#     print(tempc)
#     print(geopot)
#     print(dew)

    height = mpcalc.geopotential_to_height(geopot)
    height2 = height.to('feet')
    height[0]=sfcheight

    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(tempc.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i*1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='icon_sounding_habay_%s.png' %time2,title='ICON-EU | Habay | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   422   519   742   972  1206  1445  1690  1940  2197  3015  4238  5641
[13]  7289  9295 10494 11924 13796 16447



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   422   516   739   968  1202  1442  1687  1938  2194  3013  4235  5638
[13]  7286  9293 10491 11924 13794 16447



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2022-06-08 06:00:00
 [1]   422   613   835  1063  1296  1535  1780  2032  2292  3113  4335  5762
[13]  7449  9501 10736 12192 14001 16558



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   422   615   838  1066  1299  1538  1784  2037  2296  3118  4342  5769
[13]  7454  9504 10740 12195 14001 16558



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   422   620   842  1070  1304  1544  1790  2042  2302  3123  4349  5776
[13]  7459  9508 10744 12197 14004 16560



In [9]:
for i in range(49):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=0)
    print(timeinit)

    temp = data['t']
    rhum = data['r']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']
    #press = np.sort(press)

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    #pwat = data_sfc['tcwv']
    #deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcheight = data_sfc2['h']
    #msl =  data_sfc5['msl']

    ##############################################################

    lat = 49.5
    lon = 5.75

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #msl = msl.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    rhum = rhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcheight = sfcheight.metpy.loc[{ 'latitude': lat, 'longitude': lon}]
    #pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[17] = sfctemp
    uwind[17] = sfcuwind
    vwind[17] = sfcvwind
    #geopot[17] = sfcgeopot
    press = np.where(press == 1000 , np.round(sfcpress/100) ,press)
    #press = press*units.hPa
    #msl = (msl.data)/100*units.hPa

    #sfcpress.data=92400
    
    if sfcpress.item(0) <= 95100:
                temp = np.delete(temp,16)
                rhum = np.delete(rhum,16)
                geopot = np.delete(geopot,16)
                uwind = np.delete(uwind,16)
                vwind = np.delete(vwind,16)
                press = np.delete(press,16)
                
    if sfcpress.item(0) <= 92600:
                temp = np.delete(temp,15)
                rhum = np.delete(rhum,15)
                geopot = np.delete(geopot,15)
                uwind = np.delete(uwind,15)
                vwind = np.delete(vwind,15)
                press = np.delete(press,15)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    rhum = rhum.data[::-1]*units('percent')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    tempc = temp-273.15
    tempc = tempc.data[::-1]*units.degC
    sfcheight=sfcheight.data[::]*units.meter

    dew = mpcalc.dewpoint_from_relative_humidity(tempc, rhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    #dew[0] = sfcdew*units.degC
    #pwat = pwat.data.item()
    #pwat = pwat*units.mm
    #deg0l = deg0l.data.item()
    #deg0l = deg0l*units.meters

    #pressdiff = msl-press[0]
    #sfcheight = (np.log(msl/press[0])*8000)*units.meter

#    print(sfcheight)
#     print(press)
#     print(tempc)
#     print(geopot)
#     print(dew)

    height = mpcalc.geopotential_to_height(geopot)
    height2 = height.to('feet')
    height[0]=sfcheight

    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(tempc.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i*1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='icon_sounding_longwy_%s.png' %time2,title='ICON-EU | Longwy | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   340   520   745   974  1209  1448  1693  1944  2201  3018  4243  5646
[13]  7295  9304 10504 11931 13800 16449



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00


R[write to console]: Your display device is 10 x 6 in. 
It is recommended to use at least 10 x 7.5 in. plotting window 
or consider saving the layout into file



...

 [1]   340   618   840  1068  1302  1541  1787  2039  2299  3120  4343  5770
[13]  7456  9507 10743 12199 14004 16559



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00


R[write to console]: Your display device is 10 x 6 in. 
It is recommended to use at least 10 x 7.5 in. plotting window 
or consider saving the layout into file



 [1]   340   622   844  1072  1306  1546  1792  2044  2304  3125  4350  5777
[13]  7461  9511 10747 12201 14007 16562



In [10]:
for i in range(49):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=0)
    print(timeinit)

    temp = data['t']
    rhum = data['r']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']
    #press = np.sort(press)

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    #pwat = data_sfc['tcwv']
    #deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcheight = data_sfc2['h']
    #msl =  data_sfc5['msl']

    ##############################################################

    lat = 50.0
    lon = 5.375

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #msl = msl.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    rhum = rhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcheight = sfcheight.metpy.loc[{ 'latitude': lat, 'longitude': lon}]
    #pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[17] = sfctemp
    uwind[17] = sfcuwind
    vwind[17] = sfcvwind
    #geopot[17] = sfcgeopot
    press = np.where(press == 1000 , np.round(sfcpress/100) ,press)
    #press = press*units.hPa
    #msl = (msl.data)/100*units.hPa

    #sfcpress.data=92400
    
    if sfcpress.item(0) <= 95100:
                temp = np.delete(temp,16)
                rhum = np.delete(rhum,16)
                geopot = np.delete(geopot,16)
                uwind = np.delete(uwind,16)
                vwind = np.delete(vwind,16)
                press = np.delete(press,16)
                
    if sfcpress.item(0) <= 92600:
                temp = np.delete(temp,15)
                rhum = np.delete(rhum,15)
                geopot = np.delete(geopot,15)
                uwind = np.delete(uwind,15)
                vwind = np.delete(vwind,15)
                press = np.delete(press,15)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    rhum = rhum.data[::-1]*units('percent')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    tempc = temp-273.15
    tempc = tempc.data[::-1]*units.degC
    sfcheight=sfcheight.data[::]*units.meter

    dew = mpcalc.dewpoint_from_relative_humidity(tempc, rhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    #dew[0] = sfcdew*units.degC
    #pwat = pwat.data.item()
    #pwat = pwat*units.mm
    #deg0l = deg0l.data.item()
    #deg0l = deg0l*units.meters

    #pressdiff = msl-press[0]
    #sfcheight = (np.log(msl/press[0])*8000)*units.meter

#    print(sfcheight)
#     print(press)
#     print(tempc)
#     print(geopot)
#     print(dew)

    height = mpcalc.geopotential_to_height(geopot)
    height2 = height.to('feet')
    height[0]=sfcheight

    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(tempc.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i*1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='icon_sounding_sthubert_%s.png' %time2,title='ICON-EU | Saint-Hubert | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   473   515   738   967  1201  1441  1686  1936  2193  3011  4234  5635
[13]  7282  9286 10484 11917 13791 16445



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   473   512   735   964  1199  1438  1683  1933  2191  3009  4229  5632
[13]  7279  9283 10480 11916 13790 16445



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2022-06-08 06:00:00
 [1]   473   609   831  1059  1293  1533  1778  2031  2290  3111  4335  5763
[13]  7450  9500 10734 12189 13999 16558



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   473   611   833  1062  1296  1536  1782  2035  2294  3116  4341  5770
[13]  7455  9503 10737 12191 13999 16558



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   473   616   838  1067  1301  1541  1787  2040  2299  3120  4349  5777
[13]  7459  9506 10741 12194 14001 16559



In [11]:
for i in range(49):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=0)
    print(timeinit)

    temp = data['t']
    rhum = data['r']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']
    #press = np.sort(press)

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    #pwat = data_sfc['tcwv']
    #deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcheight = data_sfc2['h']
    #msl =  data_sfc5['msl']

    ##############################################################

    lat = 50.0
    lon = 6.5

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #msl = msl.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    rhum = rhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcheight = sfcheight.metpy.loc[{ 'latitude': lat, 'longitude': lon}]
    #pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[17] = sfctemp
    uwind[17] = sfcuwind
    vwind[17] = sfcvwind
    #geopot[17] = sfcgeopot
    press = np.where(press == 1000 , np.round(sfcpress/100) ,press)
    #press = press*units.hPa
    #msl = (msl.data)/100*units.hPa

    #sfcpress.data=92400
    
    if sfcpress.item(0) <= 95100:
                temp = np.delete(temp,16)
                rhum = np.delete(rhum,16)
                geopot = np.delete(geopot,16)
                uwind = np.delete(uwind,16)
                vwind = np.delete(vwind,16)
                press = np.delete(press,16)
                
    if sfcpress.item(0) <= 92600:
                temp = np.delete(temp,15)
                rhum = np.delete(rhum,15)
                geopot = np.delete(geopot,15)
                uwind = np.delete(uwind,15)
                vwind = np.delete(vwind,15)
                press = np.delete(press,15)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    rhum = rhum.data[::-1]*units('percent')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    tempc = temp-273.15
    tempc = tempc.data[::-1]*units.degC
    sfcheight=sfcheight.data[::]*units.meter

    dew = mpcalc.dewpoint_from_relative_humidity(tempc, rhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    #dew[0] = sfcdew*units.degC
    #pwat = pwat.data.item()
    #pwat = pwat*units.mm
    #deg0l = deg0l.data.item()
    #deg0l = deg0l*units.meters

    #pressdiff = msl-press[0]
    #sfcheight = (np.log(msl/press[0])*8000)*units.meter

#    print(sfcheight)
#     print(press)
#     print(tempc)
#     print(geopot)
#     print(dew)

    height = mpcalc.geopotential_to_height(geopot)
    height2 = height.to('feet')
    height[0]=sfcheight

    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(tempc.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i*1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='icon_sounding_bitburg_%s.png' %time2,title='ICON-EU | Bitburg | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   333   520   744   973  1208  1447  1692  1942  2199  3014  4238  5641
[13]  7290  9298 10499 11922 13795 16446



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   333   519   743   972  1206  1446  1690  1941  2198  3012  4236  5639
[13]  7289  9296 10495 11922 13796 16447



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2022-06-08 06:00:00
 [1]   333   613   836  1063  1296  1533  1777  2028  2287  3109  4325  5748
[13]  7433  9485 10719 12175 13994 16554



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   333   616   838  1066  1298  1537  1782  2033  2292  3113  4331  5756
[13]  7441  9491 10724 12180 13995 16556



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   333   619   842  1069  1302  1541  1787  2039  2299  3118  4339  5764
[13]  7448  9496 10729 12183 13997 16560



In [12]:
for i in range(49):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=0)
    print(timeinit)

    temp = data['t']
    rhum = data['r']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']
    #press = np.sort(press)

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    #pwat = data_sfc['tcwv']
    #deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcheight = data_sfc2['h']
    #msl =  data_sfc5['msl']

    ##############################################################

    lat = 49.5
    lon = 6.5625

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #msl = msl.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    rhum = rhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcheight = sfcheight.metpy.loc[{ 'latitude': lat, 'longitude': lon}]
    #pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[17] = sfctemp
    uwind[17] = sfcuwind
    vwind[17] = sfcvwind
    #geopot[17] = sfcgeopot
    press = np.where(press == 1000 , np.round(sfcpress/100) ,press)
    #press = press*units.hPa
    #msl = (msl.data)/100*units.hPa

    #sfcpress.data=92400
    
    if sfcpress.item(0) <= 95100:
                temp = np.delete(temp,16)
                rhum = np.delete(rhum,16)
                geopot = np.delete(geopot,16)
                uwind = np.delete(uwind,16)
                vwind = np.delete(vwind,16)
                press = np.delete(press,16)
                
    if sfcpress.item(0) <= 92600:
                temp = np.delete(temp,15)
                rhum = np.delete(rhum,15)
                geopot = np.delete(geopot,15)
                uwind = np.delete(uwind,15)
                vwind = np.delete(vwind,15)
                press = np.delete(press,15)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    rhum = rhum.data[::-1]*units('percent')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    tempc = temp-273.15
    tempc = tempc.data[::-1]*units.degC
    sfcheight=sfcheight.data[::]*units.meter

    dew = mpcalc.dewpoint_from_relative_humidity(tempc, rhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    #dew[0] = sfcdew*units.degC
    #pwat = pwat.data.item()
    #pwat = pwat*units.mm
    #deg0l = deg0l.data.item()
    #deg0l = deg0l*units.meters

    #pressdiff = msl-press[0]
    #sfcheight = (np.log(msl/press[0])*8000)*units.meter

#    print(sfcheight)
#     print(press)
#     print(tempc)
#     print(geopot)
#     print(dew)

    height = mpcalc.geopotential_to_height(geopot)
    height2 = height.to('feet')
    height[0]=sfcheight

    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(tempc.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i*1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='icon_sounding_mettlach_%s.png' %time2,title='ICON-EU | Mettlach | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   300   525   749   978  1213  1452  1697  1947  2204  3018  4245  5650
[13]  7300  9311 10513 11934 13802 16450



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   300   523   747   977  1211  1450  1695  1946  2203  3018  4244  5648
[13]  7299  9309 10510 11934 13803 16450



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2022-06-08 06:00:00
 [1]   300   617   840  1068  1301  1539  1782  2033  2292  3112  4329  5752
[13]  7438  9491 10726 12183 14000 16557



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   300   621   843  1071  1304  1542  1786  2038  2296  3117  4335  5760
[13]  7446  9498 10732 12188 14000 16559



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   300   624   847  1075  1308  1547  1792  2043  2302  3123  4342  5769
[13]  7453  9502 10737 12192 14002 16561



In [13]:
for i in range(49):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=0)
    print(timeinit)

    temp = data['t']
    rhum = data['r']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']
    #press = np.sort(press)

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    #pwat = data_sfc['tcwv']
    #deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcheight = data_sfc2['h']
    #msl =  data_sfc5['msl']

    ##############################################################

    lat = 49.1875
    lon = 5.375

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #msl = msl.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    rhum = rhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcheight = sfcheight.metpy.loc[{ 'latitude': lat, 'longitude': lon}]
    #pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[17] = sfctemp
    uwind[17] = sfcuwind
    vwind[17] = sfcvwind
    #geopot[17] = sfcgeopot
    press = np.where(press == 1000 , np.round(sfcpress/100) ,press)
    #press = press*units.hPa
    #msl = (msl.data)/100*units.hPa

    #sfcpress.data=92400
    
    if sfcpress.item(0) <= 95100:
                temp = np.delete(temp,16)
                rhum = np.delete(rhum,16)
                geopot = np.delete(geopot,16)
                uwind = np.delete(uwind,16)
                vwind = np.delete(vwind,16)
                press = np.delete(press,16)
                
    if sfcpress.item(0) <= 92600:
                temp = np.delete(temp,15)
                rhum = np.delete(rhum,15)
                geopot = np.delete(geopot,15)
                uwind = np.delete(uwind,15)
                vwind = np.delete(vwind,15)
                press = np.delete(press,15)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    rhum = rhum.data[::-1]*units('percent')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    tempc = temp-273.15
    tempc = tempc.data[::-1]*units.degC
    sfcheight=sfcheight.data[::]*units.meter

    dew = mpcalc.dewpoint_from_relative_humidity(tempc, rhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    #dew[0] = sfcdew*units.degC
    #pwat = pwat.data.item()
    #pwat = pwat*units.mm
    #deg0l = deg0l.data.item()
    #deg0l = deg0l*units.meters

    #pressdiff = msl-press[0]
    #sfcheight = (np.log(msl/press[0])*8000)*units.meter

#    print(sfcheight)
#     print(press)
#     print(tempc)
#     print(geopot)
#     print(dew)

    height = mpcalc.geopotential_to_height(geopot)
    height2 = height.to('feet')
    height[0]=sfcheight

    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(tempc.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i*1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='icon_sounding_verdun_%s.png' %time2,title='ICON-EU | Verdun | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   243   521   746   975  1210  1450  1695  1946  2203  3021  4245  5648
[13]  7298  9309 10510 11936 13803 16451



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   243   519   743   972  1207  1446  1691  1942  2199  3018  4241  5645
[13]  7294  9303 10501 11935 13801 16450



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2022-06-08 06:00:00
 [1]   243   617   840  1068  1301  1541  1786  2038  2298  3119  4343  5771
[13]  7459  9513 10748 12204 14011 16560



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   243   620   843  1071  1305  1545  1790  2043  2302  3123  4348  5777
[13]  7463  9516 10752 12207 14012 16561



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   243   624   847  1075  1309  1549  1795  2048  2308  3130  4355  5784
[13]  7469  9519 10756 12210 14013 16563



In [14]:
for i in range(49):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=0)
    print(timeinit)

    temp = data['t']
    rhum = data['r']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']
    #press = np.sort(press)

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    #pwat = data_sfc['tcwv']
    #deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcheight = data_sfc2['h']
    #msl =  data_sfc5['msl']

    ##############################################################

    lat = 49.5
    lon = 5.1875

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #msl = msl.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    rhum = rhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcheight = sfcheight.metpy.loc[{ 'latitude': lat, 'longitude': lon}]
    #pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[17] = sfctemp
    uwind[17] = sfcuwind
    vwind[17] = sfcvwind
    #geopot[17] = sfcgeopot
    press = np.where(press == 1000 , np.round(sfcpress/100) ,press)
    #press = press*units.hPa
    #msl = (msl.data)/100*units.hPa

    #sfcpress.data=92400
    
    if sfcpress.item(0) <= 95100:
                temp = np.delete(temp,16)
                rhum = np.delete(rhum,16)
                geopot = np.delete(geopot,16)
                uwind = np.delete(uwind,16)
                vwind = np.delete(vwind,16)
                press = np.delete(press,16)
                
    if sfcpress.item(0) <= 92600:
                temp = np.delete(temp,15)
                rhum = np.delete(rhum,15)
                geopot = np.delete(geopot,15)
                uwind = np.delete(uwind,15)
                vwind = np.delete(vwind,15)
                press = np.delete(press,15)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    rhum = rhum.data[::-1]*units('percent')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    tempc = temp-273.15
    tempc = tempc.data[::-1]*units.degC
    sfcheight=sfcheight.data[::]*units.meter

    dew = mpcalc.dewpoint_from_relative_humidity(tempc, rhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    #dew[0] = sfcdew*units.degC
    #pwat = pwat.data.item()
    #pwat = pwat*units.mm
    #deg0l = deg0l.data.item()
    #deg0l = deg0l*units.meters

    #pressdiff = msl-press[0]
    #sfcheight = (np.log(msl/press[0])*8000)*units.meter

#    print(sfcheight)
#     print(press)
#     print(tempc)
#     print(geopot)
#     print(dew)

    height = mpcalc.geopotential_to_height(geopot)
    height2 = height.to('feet')
    height[0]=sfcheight

     # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(tempc.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i*1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='icon_sounding_stenay_%s.png' %time2,title='ICON-EU | Stenay | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   212   519   743   972  1206  1446  1690  1941  2198  3017  4240  5642
[13]  7290  9296 10496 11927 13798 16448



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   212   516   740   969  1202  1442  1687  1937  2194  3012  4235  5639
[13]  7287  9292 10489 11926 13796 16448



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2022-06-08 06:00:00
 [1]   212   614   837  1065  1299  1538  1783  2036  2295  3116  4341  5770
[13]  7458  9509 10744 12202 14006 16560



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   212   616   839  1067  1302  1541  1787  2040  2300  3121  4348  5777
[13]  7462  9513 10748 12203 14007 16559



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   212   620   843  1072  1306  1546  1793  2045  2305  3126  4353  5783
[13]  7467  9516 10750 12204 14009 16562



In [15]:
for i in range(49):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=0)
    print(timeinit)

    temp = data['t']
    rhum = data['r']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']
    #press = np.sort(press)

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    #pwat = data_sfc['tcwv']
    #deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcheight = data_sfc2['h']
    #msl =  data_sfc5['msl']

    ##############################################################

    lat = 50.5
    lon = 5.875

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #msl = msl.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    rhum = rhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcheight = sfcheight.metpy.loc[{ 'latitude': lat, 'longitude': lon}]
    #pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[17] = sfctemp
    uwind[17] = sfcuwind
    vwind[17] = sfcvwind
    #geopot[17] = sfcgeopot
    press = np.where(press == 1000 , np.round(sfcpress/100) ,press)
    #press = press*units.hPa
    #msl = (msl.data)/100*units.hPa

    #sfcpress.data=92400
    
    if sfcpress.item(0) <= 95100:
                temp = np.delete(temp,16)
                rhum = np.delete(rhum,16)
                geopot = np.delete(geopot,16)
                uwind = np.delete(uwind,16)
                vwind = np.delete(vwind,16)
                press = np.delete(press,16)
                
    if sfcpress.item(0) <= 92600:
                temp = np.delete(temp,15)
                rhum = np.delete(rhum,15)
                geopot = np.delete(geopot,15)
                uwind = np.delete(uwind,15)
                vwind = np.delete(vwind,15)
                press = np.delete(press,15)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    rhum = rhum.data[::-1]*units('percent')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    tempc = temp-273.15
    tempc = tempc.data[::-1]*units.degC
    sfcheight=sfcheight.data[::]*units.meter

    dew = mpcalc.dewpoint_from_relative_humidity(tempc, rhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    #dew[0] = sfcdew*units.degC
    #pwat = pwat.data.item()
    #pwat = pwat*units.mm
    #deg0l = deg0l.data.item()
    #deg0l = deg0l*units.meters

    #pressdiff = msl-press[0]
    #sfcheight = (np.log(msl/press[0])*8000)*units.meter

#    print(sfcheight)
#     print(press)
#     print(tempc)
#     print(geopot)
#     print(dew)

    height = mpcalc.geopotential_to_height(geopot)
    height2 = height.to('feet')
    height[0]=sfcheight

    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(tempc.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i*1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='icon_sounding_spa_%s.png' %time2,title='ICON-EU | Spa | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   351   511   735   965  1199  1439  1684  1935  2192  3008  4229  5631
[13]  7275  9276 10474 11908 13786 16442



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   351   509   733   963  1197  1436  1681  1932  2189  3005  4226  5628
[13]  7274  9275 10472 11909 13786 16442



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2022-06-08 06:00:00
 [1]   351   604   826  1054  1287  1527  1772  2025  2284  3104  4325  5751
[13]  7436  9486 10719 12174 13991 16554



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   351   607   829  1057  1291  1531  1776  2028  2288  3109  4332  5759
[13]  7443  9490 10723 12178 13991 16555



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   351   611   834  1062  1296  1536  1781  2034  2293  3114  4339  5766
[13]  7449  9494 10727 12180 13993 16559



In [16]:
for i in range(49):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=0)
    print(timeinit)

    temp = data['t']
    rhum = data['r']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']
    #press = np.sort(press)

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    #pwat = data_sfc['tcwv']
    #deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcheight = data_sfc2['h']
    #msl =  data_sfc5['msl']

    ##############################################################

    lat = 50
    lon = 5.9375

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #msl = msl.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    rhum = rhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcheight = sfcheight.metpy.loc[{ 'latitude': lat, 'longitude': lon}]
    #pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[17] = sfctemp
    uwind[17] = sfcuwind
    vwind[17] = sfcvwind
    #geopot[17] = sfcgeopot
    press = np.where(press == 1000 , np.round(sfcpress/100) ,press)
    #press = press*units.hPa
    #msl = (msl.data)/100*units.hPa

    #sfcpress.data=92400
    
    if sfcpress.item(0) <= 95100:
                temp = np.delete(temp,16)
                rhum = np.delete(rhum,16)
                geopot = np.delete(geopot,16)
                uwind = np.delete(uwind,16)
                vwind = np.delete(vwind,16)
                press = np.delete(press,16)
                
    if sfcpress.item(0) <= 92600:
                temp = np.delete(temp,15)
                rhum = np.delete(rhum,15)
                geopot = np.delete(geopot,15)
                uwind = np.delete(uwind,15)
                vwind = np.delete(vwind,15)
                press = np.delete(press,15)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    rhum = rhum.data[::-1]*units('percent')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    tempc = temp-273.15
    tempc = tempc.data[::-1]*units.degC
    sfcheight=sfcheight.data[::]*units.meter

    dew = mpcalc.dewpoint_from_relative_humidity(tempc, rhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    #dew[0] = sfcdew*units.degC
    #pwat = pwat.data.item()
    #pwat = pwat*units.mm
    #deg0l = deg0l.data.item()
    #deg0l = deg0l*units.meters

    #pressdiff = msl-press[0]
    #sfcheight = (np.log(msl/press[0])*8000)*units.meter

#    print(sfcheight)
#     print(press)
#     print(tempc)
#     print(geopot)
#     print(dew)

    height = mpcalc.geopotential_to_height(geopot)
    height2 = height.to('feet')
    height[0]=sfcheight

    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(tempc.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i*1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='icon_sounding_wiltz_%s.png' %time2,title='ICON-EU | Wiltz | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   420   517   741   970  1204  1444  1689  1939  2196  3012  4236  5639
[13]  7286  9290 10490 11920 13793 16445



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   420   515   739   968  1203  1442  1687  1937  2194  3010  4233  5635
[13]  7284  9290 10488 11919 13793 16445



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2022-06-08 06:00:00
 [1]   420   612   834  1061  1294  1533  1778  2030  2288  3110  4329  5755
[13]  7442  9494 10727 12183 13997 16556



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   420   613   835  1063  1297  1536  1782  2034  2293  3114  4337  5763
[13]  7448  9497 10730 12187 13998 16557



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-08 06:00:00
 [1]   420   617   839  1067  1302  1541  1787  2039  2299  3120  4345  5770
[13]  7454  9501 10736 12190 13999 16560



In [3]:
for i in range(49):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=0)
    print(timeinit)

    temp = data['t']
    rhum = data['r']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']
    #press = np.sort(press)

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    #pwat = data_sfc['tcwv']
    #deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcheight = data_sfc2['h']
    #msl =  data_sfc5['msl']

    ##############################################################

    lat = 49.6875
    lon = 7.375

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #msl = msl.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    rhum = rhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcheight = sfcheight.metpy.loc[{ 'latitude': lat, 'longitude': lon}]
    #pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    #deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[17] = sfctemp
    uwind[17] = sfcuwind
    vwind[17] = sfcvwind
    #geopot[17] = sfcgeopot
    press = np.where(press == 1000 , np.round(sfcpress/100) ,press)
    #press = press*units.hPa
    #msl = (msl.data)/100*units.hPa

    #sfcpress.data=92400
    
    if sfcpress.item(0) <= 95100:
                temp = np.delete(temp,16)
                rhum = np.delete(rhum,16)
                geopot = np.delete(geopot,16)
                uwind = np.delete(uwind,16)
                vwind = np.delete(vwind,16)
                press = np.delete(press,16)
                
    if sfcpress.item(0) <= 92600:
                temp = np.delete(temp,15)
                rhum = np.delete(rhum,15)
                geopot = np.delete(geopot,15)
                uwind = np.delete(uwind,15)
                vwind = np.delete(vwind,15)
                press = np.delete(press,15)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    rhum = rhum.data[::-1]*units('percent')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    tempc = temp-273.15
    tempc = tempc.data[::-1]*units.degC
    sfcheight=sfcheight.data[::]*units.meter

    dew = mpcalc.dewpoint_from_relative_humidity(tempc, rhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    #dew[0] = sfcdew*units.degC
    #pwat = pwat.data.item()
    #pwat = pwat*units.mm
    #deg0l = deg0l.data.item()
    #deg0l = deg0l*units.meters

    #pressdiff = msl-press[0]
    #sfcheight = (np.log(msl/press[0])*8000)*units.meter

#    print(sfcheight)
#     print(press)
#     print(tempc)
#     print(geopot)
#     print(dew)

    height = mpcalc.geopotential_to_height(geopot)
    height2 = height.to('feet')
    height[0]=sfcheight

    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(tempc.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i*1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='icon_sounding_idarob_%s.png' %time2,title='ICON-EU | Idar-Oberstein | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-09 12:00:00
 [1]   411   574   797  1025  1257  1495  1738  1987  2243  3052  4250  5625
[13]  7247  9277 10514 12002 13893 16522



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-09 12:00:00
 [1]   411   578   802  1030  1262  1500  1744  1993  2249  3058  4257  5633
[13]  7258  9291 10529 12015 13906 16529



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2022-06-09 12:00:00
 [1]   411   639   866  1098  1335  1577  1824  2077  2337  3164  4397  5814
[13]  7481  9511 10727 12162 13988 16567



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-09 12:00:00
 [1]   411   638   866  1098  1335  1577  1825  2079  2338  3164  4398  5815
[13]  7482  9511 10726 12160 13988 16569



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-09 12:00:00
 [1]   411   636   864  1097  1335  1577  1825  2078  2339  3164  4398  5815
[13]  7481  9509 10723 12156 13988 16571

